In [1]:
# This Python 3 environment comes with many helpful analytics libraries installed
# It is defined by the kaggle/python Docker image: https://github.com/kaggle/docker-python
# For example, here's several helpful packages to load

import numpy as np # linear algebra
import pandas as pd # data processing, CSV file I/O (e.g. pd.read_csv)

# Input data files are available in the read-only "../input/" directory
# For example, running this (by clicking run or pressing Shift+Enter) will list all files under the input directory

import os
for dirname, _, filenames in os.walk('/kaggle/input'):
    for filename in filenames:
        print(os.path.join(dirname, filename))

# You can write up to 20GB to the current directory (/kaggle/working/) that gets preserved as output when you create a version using "Save & Run All" 
# You can also write temporary files to /kaggle/temp/, but they won't be saved outside of the current session

# Introduction

### Modeling Atomic Structures with Dynamic Visualization in Plotly and Cube4D

This notebook explores the realistic modeling of atomic structures, specifically a water molecule (H₂O), using 3D visualization techniques in Plotly and dynamic state representation in Cube4D. The goal is to represent atomic components like the nucleus, protons, neutrons, and electron clouds with proportionate scaling and accurate positional dynamics. By simulating probabilistic electron cloud distributions, this model provides an enhanced, interactive visualization of atomic behavior over time.

### Key Components of the Model

1. **Nucleus Representation**:
   - The nucleus of each atom is depicted as a dense structure of **protons** and **neutrons** positioned around a central point.
   - Protons and neutrons are represented by distinct colors (red and blue) to emphasize their presence and density within the nucleus.

2. **Electron Cloud Visualization**:
   - Instead of static orbits, electrons are visualized as a **probabilistic cloud** surrounding the nucleus, where density reflects the likelihood of finding an electron in specific regions.
   - This electron cloud expands outward from the nucleus, representing the dynamic nature of electron distributions in a realistic manner.

3. **Zoom-Responsive Scaling**:
   - By implementing orthographic projection and size adjustments, the model maintains visual accuracy regardless of zoom level, ensuring the nucleus and electron cloud scale proportionately as the viewer zooms in or out.

### Objectives

The primary objective of this notebook is to present a scientifically accurate visualization of atomic structures using:
- Real-time dynamic state transitions to demonstrate the electron cloud's probabilistic behavior.
- Proportionate scaling to maintain visual integrity across different zoom levels.
- A modular approach with Cube4D for future expansion into complex molecular structures and quantum behavior modeling.

### Approach and Techniques

This model leverages a 4D relational matrix (Cube4D) for dynamic state changes, enabling the representation of quantum properties over time without the need for extensive scene rendering. This approach allows efficient modeling of:
- Electron movement and probabilistic distribution using a dynamic radius decay function.
- State transitions such as "ground" and "excited" states that visually alter the electron cloud's characteristics.

By combining Plotly's interactive 3D capabilities with Cube4D's state management, this notebook offers an engaging, educational tool for visualizing atomic structure and behavior in a scientifically grounded manner.

---

# Conclusion

### Summary of Achievements

In this notebook, we have successfully created an interactive and scientifically accurate 3D model of atomic structure, focusing on a water molecule. The model demonstrates:
- A detailed **nucleus structure** with individual protons and neutrons for realism.
- A **probabilistic electron cloud** to illustrate electron behavior around the nucleus.
- **Proportionate scaling** that adjusts dynamically with zoom, preserving the model's structural integrity at various magnifications.

### Future Applications and Extensions

This foundational approach to atomic modeling can be extended to more complex molecular structures, quantum phenomena, and other atomic behaviors, including:
- **Multi-atomic and complex molecule visualization** for biological or chemical applications.
- **Quantum entanglement modeling** with dynamic state changes for advanced studies.
- **Enhanced interactive features** such as real-time state transitions or electron density fluctuations in response to environmental variables.

### Final Thoughts

By implementing this model, we have bridged visualization and scientific accuracy, providing an immersive experience in understanding atomic structures. The integration of Cube4D state management enables future explorations into complex quantum behaviors, setting the stage for advancements in molecular modeling, educational simulations, and real-time atomic interaction analysis.

This notebook serves as a robust platform for visualizing the microcosmic world of atoms, supporting deeper insights into atomic properties, molecular formation, and quantum principles.

---

*Enjoy exploring the atomic world and its intricacies with this interactive model!*

In [2]:
import plotly.graph_objects as go
import numpy as np

# Parameters for atomic structure
nucleus_radius = 0.2   # Smaller radius for nucleus
cloud_radius = 1.0     # Larger radius for electron cloud around nucleus
num_protons = 8        # Example: Oxygen nucleus
num_neutrons = 8       # Example: Oxygen nucleus
num_cloud_points = 200 # Number of points in the electron cloud
num_frames = 100       # Number of frames for animation

# Generate positions for protons and neutrons in the nucleus
np.random.seed(0)  # Ensure reproducibility
def generate_nucleus_positions(num_particles, radius):
    r = np.random.uniform(0, radius, num_particles)
    theta = np.random.uniform(0, 2 * np.pi, num_particles)
    phi = np.random.uniform(0, np.pi, num_particles)
    
    x = r * np.sin(phi) * np.cos(theta)
    y = r * np.sin(phi) * np.sin(theta)
    z = r * np.cos(phi)
    return x, y, z

# Generate positions for the electron cloud
def generate_electron_cloud(radius, num_points):
    r = np.random.normal(loc=radius, scale=0.3 * radius, size=num_points)
    theta = np.random.uniform(0, 2 * np.pi, num_points)
    phi = np.random.uniform(0, np.pi, num_points)
    
    x = r * np.sin(phi) * np.cos(theta)
    y = r * np.sin(phi) * np.sin(theta)
    z = r * np.cos(phi)
    return x, y, z

# Generate nucleus particle positions
proton_x, proton_y, proton_z = generate_nucleus_positions(num_protons, nucleus_radius)
neutron_x, neutron_y, neutron_z = generate_nucleus_positions(num_neutrons, nucleus_radius)

# Create initial frames for animation
frames = []
for i in range(num_frames):
    # Update electron cloud positions to create a dynamic effect
    electron_cloud_x, electron_cloud_y, electron_cloud_z = generate_electron_cloud(cloud_radius, num_cloud_points)
    
    # Nucleus with protons and neutrons
    nucleus_protons = go.Scatter3d(
        x=proton_x, y=proton_y, z=proton_z,
        mode='markers',
        marker=dict(size=5, color='red', opacity=0.8),
        name="Protons"
    )
    nucleus_neutrons = go.Scatter3d(
        x=neutron_x, y=neutron_y, z=neutron_z,
        mode='markers',
        marker=dict(size=5, color='blue', opacity=0.8),
        name="Neutrons"
    )
    
    # Electron cloud
    electron_cloud = go.Scatter3d(
        x=electron_cloud_x, y=electron_cloud_y, z=electron_cloud_z,
        mode='markers',
        marker=dict(size=2, color='yellow', opacity=0.3),
        hoverinfo='skip',
        name="Electron Cloud"
    )
    
    # Add to frames
    frames.append(go.Frame(data=[nucleus_protons, nucleus_neutrons, electron_cloud], name=str(i)))

# Layout with dark background and perspective settings
layout = go.Layout(
    title="Nucleus and Electron Cloud with Dynamic Scaling",
    scene=dict(
        xaxis=dict(range=[-2, 2], visible=False, showgrid=False, showline=False, zeroline=False),
        yaxis=dict(range=[-2, 2], visible=False, showgrid=False, showline=False, zeroline=False),
        zaxis=dict(range=[-2, 2], visible=False, showgrid=False, showline=False, zeroline=False),
        aspectmode="manual",
        aspectratio=dict(x=1, y=1, z=1),
        camera=dict(
            eye=dict(x=1.25, y=1.25, z=1.25),
            projection=dict(type="orthographic") # Orthographic projection for consistent scaling
        ),
        bgcolor="black"  # Dark background color
    ),
    updatemenus=[
        dict(
            type="buttons",
            showactive=False,
            buttons=[
                dict(label="Play", method="animate", args=[None, {"frame": {"duration": 50, "redraw": False},
                                                                 "fromcurrent": True, "mode": "immediate"}]),
                dict(label="Pause", method="animate", args=[[None], {"mode": "immediate", "frame": {"duration": 0, "redraw": False}, "transition": {"duration": 0}}])
            ]
        )
    ],
    sliders=[{
        "active": 0,
        "yanchor": "top",
        "xanchor": "left",
        "currentvalue": {
            "prefix": "Frame: ",
            "font": {"size": 20}
        },
        "pad": {"b": 10, "t": 50},
        "len": 0.9,
        "x": 0.1,
        "y": 0,
        "steps": [{"method": "animate", "label": str(k), "args": [[str(k)], {"frame": {"duration": 50, "redraw": False}, "mode": "immediate"}]} for k in range(num_frames)]
    }]
)

# Initial data with nucleus and electron cloud
initial_data = [frames[0].data[0], frames[0].data[1], frames[0].data[2]]

# Create figure with frames
fig = go.Figure(data=initial_data, frames=frames, layout=layout)

# Show animation
fig.show()

## License

This notebook is licensed under the **Creative Commons Attribution-NonCommercial-ShareAlike 4.0 International (CC BY-NC-SA 4.0)** license.

- **Attribution**: You must give appropriate credit, provide a link to the license, and indicate if changes were made. You may do so in any reasonable manner, but not in any way that suggests the licensor endorses you or your use.
- **NonCommercial**: You may not use the material for commercial purposes.
- **ShareAlike**: If you remix, transform, or build upon the material, you must distribute your contributions under the same license as the original.

For more details, see the [CC BY-NC-SA 4.0 License](https://creativecommons.org/licenses/by-nc-sa/4.0/).